# 1.라이브러리 임포트

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

%matplotlib inline

import koreanize_matplotlib


# 2.데이터 가져오기

### 2.1 kaggle 라벨링 완료된 데이터

In [2]:
df = pd.read_csv('../data/SeoulBikeData_labeling_fin1.csv', encoding='cp949')
df

Date  Year  Month  Day  Rented Bike Count  Hour  Temperature(℃)  \
0     2017-12-01  2017     12    1                254     0            -5.2   
1     2017-12-01  2017     12    1                204     1            -5.5   
2     2017-12-01  2017     12    1                173     2            -6.0   
3     2017-12-01  2017     12    1                107     3            -6.2   
4     2017-12-01  2017     12    1                 78     4            -6.0   
...          ...   ...    ...  ...                ...   ...             ...   
8755  2018-11-30  2018     11   30               1003    19             4.2   
8756  2018-11-30  2018     11   30                764    20             3.4   
8757  2018-11-30  2018     11   30                694    21             2.6   
8758  2018-11-30  2018     11   30                712    22             2.1   
8759  2018-11-30  2018     11   30                584    23             1.9   

      Humidity(%)  Wind speed (m/s)  Visibility (10m)  \
0              37               2.2              2000   
1              38               0.8              2000   
2              39               1.0              2000   
3              40               0.9              2000   
4              36               2.3              2000   
...           ...               ...               ...   
8755           34               2.6              1894   
8756           37               2.3              2000   
8757           39               0.3              1968   
8758           41               1.0              1859   
8759           43               1.3              1909   

      Dew point temperature(℃)  Solar Radiation (MJ/m2)  Rainfall(mm)  \
0                        -17.6                      0.0           0.0   
1                        -17.6                      0.0           0.0   
2                        -17.7                      0.0           0.0   
3                        -17.6                      0.0           0.0   
4                        -18.6                      0.0           0.0   
...                        ...                      ...           ...   
8755                     -10.3                      0.0           0.0   
8756                      -9.9                      0.0           0.0   
8757                      -9.9                      0.0           0.0   
8758                      -9.8                      0.0           0.0   
8759                      -9.3                      0.0           0.0   

      Snowfall (cm) Seasons     Holiday Day of Week Weekend  
0               0.0  Winter  No Holiday      Friday      No  
1               0.0  Winter  No Holiday      Friday      No  
2               0.0  Winter  No Holiday      Friday      No  
3               0.0  Winter  No Holiday      Friday      No  
4               0.0  Winter  No Holiday      Friday      No  
...             ...     ...         ...         ...     ...  
8755            0.0  Autumn  No Holiday      Friday      No  
8756            0.0  Autumn  No Holiday      Friday      No  
8757            0.0  Autumn  No Holiday      Friday      No  
8758            0.0  Autumn  No Holiday      Friday      No  
8759            0.0  Autumn  No Holiday      Friday      No  

[8760 rows x 18 columns]

In [3]:
df['Rented Bike Count'].tail(24).sum()

16297

### 2.2 2018-12-01 부터 2023-12-31 날짜 데이터 생성

#### 2.2.1 'Date' 컬럼 생성

In [4]:
df_new = pd.DataFrame(
    {'Date': pd.date_range(start='2018-11-30', 
                           end='2024-01-01',
                           freq='H',
                           closed='right')})

df_new

/var/folders/cy/sw8s66dd02l8b9dj7pqk2ljm0000gn/T/ipykernel_2047/1863162637.py:2: FutureWarning: Argument `closed` is deprecated in favor of `inclusive`.
  {'Date': pd.date_range(start='2018-11-30',


Date
0     2018-11-30 01:00:00
1     2018-11-30 02:00:00
2     2018-11-30 03:00:00
3     2018-11-30 04:00:00
4     2018-11-30 05:00:00
...                   ...
44587 2023-12-31 20:00:00
44588 2023-12-31 21:00:00
44589 2023-12-31 22:00:00
44590 2023-12-31 23:00:00
44591 2024-01-01 00:00:00

[44592 rows x 1 columns]

#### 2.2.2 'Date' 컬럼 타입 string으로 변환

In [5]:
df_new['Date'] = df_new['Date'].astype(str)

#### 2.2.3 'Date' 컬럼에서 'Year','Month','Day' 컬럼 분할

In [6]:
date_split = df_new['Date'].str.split(' ')
date_list = date_split.str.get(0)
hour_list = date_split.str.get(1)

df_new['Year'] = date_list.str.split('-').str.get(0)
df_new['Month'] = date_list.str.split('-').str.get(1)
df_new['Day'] = date_list.str.split('-').str.get(2)
df_new['Hour'] = hour_list.str.split(':').str.get(0)

df_new

Date  Year Month Day Hour
0      2018-11-30 01:00:00  2018    11  30   01
1      2018-11-30 02:00:00  2018    11  30   02
2      2018-11-30 03:00:00  2018    11  30   03
3      2018-11-30 04:00:00  2018    11  30   04
4      2018-11-30 05:00:00  2018    11  30   05
...                    ...   ...   ...  ..  ...
44587  2023-12-31 20:00:00  2023    12  31   20
44588  2023-12-31 21:00:00  2023    12  31   21
44589  2023-12-31 22:00:00  2023    12  31   22
44590  2023-12-31 23:00:00  2023    12  31   23
44591  2024-01-01 00:00:00  2024    01  01   00

[44592 rows x 5 columns]

### 2.3 2018-12-01 부터 2023-12-31까지의 날씨 데이터 생성

In [7]:
# temp_18 = pd.read_csv('../weather_data/20240111182300/weather_data/20240111182300/청운효자동_기온_202301_202312.csv', encoding='cp949')
# humid_18 = pd.read_csv('../weather_data/2024')
# wind_18 = pd.


In [8]:
# import os

# folder_list = ['20240111182300','20240111182159','20240111181759','20240111181508','20240111181349','20240111181127']

# base_url = '../weather_data/'

# count = 0
# while count < 6:
#     folder_name = folder_list[i]
#     url = f'{base_url}{folder_name}'

#     folder = os.listdir(url)

#     os.chdir(base_url)

#     df_weather = pd.DataFrame()

#     for files in folder:
#         df = pd.read_csv(files, encoding='cp949')
#         df_weather = pd.concat([df_weather, df], axis=1, ignore_index=True)
    
#     df_weather.to_csv(base_url + 'weather_data' + f'{count}')
    
#     count += 1

### 2.4 2018-12-01부터 2023-12-31까지의 계절, 요일 데이터 생성

#### 2.4.1 'Seasons' 컬럼 생성

In [9]:
df_new['Seasons'] = df_new['Month'].astype(int)

def map_season(month):
    if 3 <= month <= 5:
        return 'Spring'
    elif 6 <= month <= 8:
        return 'Summer'
    elif 9 <= month <= 11:
        return 'Autumn'
    else:
        return 'Winter'

df_new['Seasons'] = df_new['Seasons'].apply(map_season)

df_new

Date  Year Month Day Hour Seasons
0      2018-11-30 01:00:00  2018    11  30   01  Autumn
1      2018-11-30 02:00:00  2018    11  30   02  Autumn
2      2018-11-30 03:00:00  2018    11  30   03  Autumn
3      2018-11-30 04:00:00  2018    11  30   04  Autumn
4      2018-11-30 05:00:00  2018    11  30   05  Autumn
...                    ...   ...   ...  ..  ...     ...
44587  2023-12-31 20:00:00  2023    12  31   20  Winter
44588  2023-12-31 21:00:00  2023    12  31   21  Winter
44589  2023-12-31 22:00:00  2023    12  31   22  Winter
44590  2023-12-31 23:00:00  2023    12  31   23  Winter
44591  2024-01-01 00:00:00  2024    01  01   00  Winter

[44592 rows x 6 columns]

#### 2.4.2 'Holiday' 컬럼 생성

In [10]:
#!pip install holidays

In [11]:
import holidays

hol = holidays.KR()

df_new['Holiday'] = df_new['Date'].apply(lambda x: 'Holiday' if x in hol else 'No Holiday')

df_new


Date  Year Month Day Hour Seasons     Holiday
0      2018-11-30 01:00:00  2018    11  30   01  Autumn  No Holiday
1      2018-11-30 02:00:00  2018    11  30   02  Autumn  No Holiday
2      2018-11-30 03:00:00  2018    11  30   03  Autumn  No Holiday
3      2018-11-30 04:00:00  2018    11  30   04  Autumn  No Holiday
4      2018-11-30 05:00:00  2018    11  30   05  Autumn  No Holiday
...                    ...   ...   ...  ..  ...     ...         ...
44587  2023-12-31 20:00:00  2023    12  31   20  Winter  No Holiday
44588  2023-12-31 21:00:00  2023    12  31   21  Winter  No Holiday
44589  2023-12-31 22:00:00  2023    12  31   22  Winter  No Holiday
44590  2023-12-31 23:00:00  2023    12  31   23  Winter  No Holiday
44591  2024-01-01 00:00:00  2024    01  01   00  Winter     Holiday

[44592 rows x 7 columns]

#### 2.4.3 'Day of Week' 컬럼 생성

In [12]:
df_new['Day of Week'] = pd.to_datetime(df_new['Date']).dt.day_name()

df_new

Date  Year Month Day Hour Seasons     Holiday  \
0      2018-11-30 01:00:00  2018    11  30   01  Autumn  No Holiday   
1      2018-11-30 02:00:00  2018    11  30   02  Autumn  No Holiday   
2      2018-11-30 03:00:00  2018    11  30   03  Autumn  No Holiday   
3      2018-11-30 04:00:00  2018    11  30   04  Autumn  No Holiday   
4      2018-11-30 05:00:00  2018    11  30   05  Autumn  No Holiday   
...                    ...   ...   ...  ..  ...     ...         ...   
44587  2023-12-31 20:00:00  2023    12  31   20  Winter  No Holiday   
44588  2023-12-31 21:00:00  2023    12  31   21  Winter  No Holiday   
44589  2023-12-31 22:00:00  2023    12  31   22  Winter  No Holiday   
44590  2023-12-31 23:00:00  2023    12  31   23  Winter  No Holiday   
44591  2024-01-01 00:00:00  2024    01  01   00  Winter     Holiday   

      Day of Week  
0          Friday  
1          Friday  
2          Friday  
3          Friday  
4          Friday  
...           ...  
44587      Sunday  
44588      Sunday  
44589      Sunday  
44590      Sunday  
44591      Monday  

[44592 rows x 8 columns]

#### 2.4.4 'Weekend' 컬럼 생성

In [13]:
def map_weekend(x):
    if x == 'Saturday':
        return 'Yes'
    elif x == 'Sunday':
        return 'Yes'
    else:
        return 'No'

df_new['Weekend'] = df_new['Day of Week'].apply(lambda x: map_weekend(x))

df_new

Date  Year Month Day Hour Seasons     Holiday  \
0      2018-11-30 01:00:00  2018    11  30   01  Autumn  No Holiday   
1      2018-11-30 02:00:00  2018    11  30   02  Autumn  No Holiday   
2      2018-11-30 03:00:00  2018    11  30   03  Autumn  No Holiday   
3      2018-11-30 04:00:00  2018    11  30   04  Autumn  No Holiday   
4      2018-11-30 05:00:00  2018    11  30   05  Autumn  No Holiday   
...                    ...   ...   ...  ..  ...     ...         ...   
44587  2023-12-31 20:00:00  2023    12  31   20  Winter  No Holiday   
44588  2023-12-31 21:00:00  2023    12  31   21  Winter  No Holiday   
44589  2023-12-31 22:00:00  2023    12  31   22  Winter  No Holiday   
44590  2023-12-31 23:00:00  2023    12  31   23  Winter  No Holiday   
44591  2024-01-01 00:00:00  2024    01  01   00  Winter     Holiday   

      Day of Week Weekend  
0          Friday      No  
1          Friday      No  
2          Friday      No  
3          Friday      No  
4          Friday      No  
...           ...     ...  
44587      Sunday     Yes  
44588      Sunday     Yes  
44589      Sunday     Yes  
44590      Sunday     Yes  
44591      Monday      No  

[44592 rows x 9 columns]

### 2.5 2018-01-01부터 2023-12-31까지의 대여건수 데이터 생성

In [14]:
# import requests
# import json
# from datetime import datetime, timedelta

# api_key = '4f636368566d756e31303274464d5843'

# start = '2018-01-01 00:00:00'
# end = '2024-01-01 00:00:00'

# start_date = datetime.strptime(start, '%Y-%m-%d %H:%M:%S')
# end_date = datetime.strptime(end, '%Y-%m-%d %H:%M:%S')

# while start_date <= end_date:
#     RENT_DT = start_date.strftime('%Y-%m-%d/%H')
#     url = 'http://openapi.seoul.go.kr:8088/{api_key}/json/tbCycleRentData/1/500/{RENT_DT}'

#     response = requests.get(url)
#     rental_data = response.content

#     file_path = '../rental_data/rental_data{RENT_DT}.json'
#     rental_data_str  = rental_data.decode("utf-8")

#     with open(file_path, "w", encoding='utf-8') as file:
#         file.write(rental_data_str)
        
#     start_date += timedelta(hours=1)

In [15]:
# url = 'http://openapi.seoul.go.kr:8088/4f636368566d756e31303274464d5843/json/tbCycleRentData/1/1000/2018-01-01/00'

# response = requests.get(url)
# rental_data = response.content

In [16]:
# file_path = '../rental_data/rental_history_data1.json'

# rental_data_str = rental_data.decode('utf-8')

# with open(file_path, 'w', encoding='utf-8') as file:
#     file.write(rental_data_str)

In [17]:
# import requests
# from datetime import datetime, timedelta
# import json

# base_url = 'http://openapi.seoul.go.kr:8088/4f636368566d756e31303274464d5843/json/tbCycleRentData/1/500/'

# start_datetime = datetime.strptime('2018-01-01 00:00:00', '%Y-%m-%d %H:%M:%S')
# end_datetime = datetime.strptime('2024-01-01 00:00:00', '%Y-%m-%d %H:%M:%S')

# current_datetime = start_datetime
# file_path = '../rental_data/rental_history_data.json'

# while current_datetime <= end_datetime:
#     formatted_date = current_datetime.strftime('%Y-%m-%d/%H')
#     url = f'{base_url}{formatted_date}'

#     response = requests.get(url)

#     if response.status_code == 200:
#         try:
#             rental_data = response.json()  # Assuming the response is in JSON format
#             rental_data_str = json.dumps(rental_data, ensure_ascii=False)

#             with open(file_path, 'a', encoding='utf-8') as file:
#                 file.write(rental_data_str + '\n')  # Append data to the file
#         except json.JSONDecodeError as e:
#             print(f'Error decoding JSON for {formatted_date}: {e}')
#     else:
#         print(f'Error fetching data for {formatted_date}: {response.status_code}')

#     current_datetime += timedelta(hours=1)

# print('Data retrieval completed.')


In [18]:
# import json

# file = open('../rental_data/rental_history_data.json')
# rental_data = json.load(file)
# rental_history_df = pd.json_normalize(rental_data['rentData']['row'])
# rental_history_df.head(10)

In [19]:
import json

N = 30
with open('../rental_data/rental_history_data.json', encoding='utf-8') as myfile:
    head = [next(myfile) for x in range(N)]

print(head)

for i in head:
    print(i)

['{"rentData": {"list_total_count": "279", "RESULT": {"CODE": "INFO-000", "MESSAGE": "정상 처리되었습니다."}, "row": [{"BIKE_ID": "SPB-01217", "RENT_DT": "2018-01-01 00:01:33", "RENT_ID": "02003", "RENT_NM": "사육신공원앞", "RENT_HOLD": "8", "RTN_DT": "2018-01-01 00:03:14", "RTN_ID": "02003", "RTN_NM": "사육신공원앞", "RTN_HOLD": "8", "USE_MIN": "1", "USE_DST": "0.00", "USR_CLS_CD": "USR_001", "SEX_CD": "M", "BIRTH_YEAR": "1990", "RENT_STATION_ID": "ST-877", "RETURN_STATION_ID": "ST-877", "BIKE_SE_CD": "LCD자전거", "START_INDEX": 0, "END_INDEX": 0, "RNUM": "1"}, {"BIKE_ID": "SPB-02041", "RENT_DT": "2018-01-01 00:00:10", "RENT_ID": "00227", "RENT_NM": "양평2나들목 보행통로 입구", "RENT_HOLD": "9", "RTN_DT": "2018-01-01 00:04:03", "RTN_ID": "00227", "RTN_NM": "양평2나들목 보행통로 입구", "RTN_HOLD": "9", "USE_MIN": "3", "USE_DST": "50.00", "USR_CLS_CD": "USR_001", "SEX_CD": "F", "BIRTH_YEAR": "1990", "RENT_STATION_ID": "ST-277", "RETURN_STATION_ID": "ST-277", "BIKE_SE_CD": "LCD자전거", "START_INDEX": 0, "END_INDEX": 0, "RNUM": "2"}, {"

### 3. 데이터 합치기

#### 3.1 kaggle 데이터 가져오기

In [53]:
df_kaggle = pd.read_csv('../data/SeoulBikeData_labeling_fin1.csv', encoding='cp949')

#df_kaggle['Date'] = pd.to_datetime(df['Date'] + ' ' + df['Hour'] + ':00:00', format='%Y-%m-%d %H:%M:%S')

df_kaggle

Date  Year  Month  Day  Rented Bike Count  Hour  Temperature(℃)  \
0     2017-12-01  2017     12    1                254     0            -5.2   
1     2017-12-01  2017     12    1                204     1            -5.5   
2     2017-12-01  2017     12    1                173     2            -6.0   
3     2017-12-01  2017     12    1                107     3            -6.2   
4     2017-12-01  2017     12    1                 78     4            -6.0   
...          ...   ...    ...  ...                ...   ...             ...   
8755  2018-11-30  2018     11   30               1003    19             4.2   
8756  2018-11-30  2018     11   30                764    20             3.4   
8757  2018-11-30  2018     11   30                694    21             2.6   
8758  2018-11-30  2018     11   30                712    22             2.1   
8759  2018-11-30  2018     11   30                584    23             1.9   

      Humidity(%)  Wind speed (m/s)  Visibility (10m)  \
0              37               2.2              2000   
1              38               0.8              2000   
2              39               1.0              2000   
3              40               0.9              2000   
4              36               2.3              2000   
...           ...               ...               ...   
8755           34               2.6              1894   
8756           37               2.3              2000   
8757           39               0.3              1968   
8758           41               1.0              1859   
8759           43               1.3              1909   

      Dew point temperature(℃)  Solar Radiation (MJ/m2)  Rainfall(mm)  \
0                        -17.6                      0.0           0.0   
1                        -17.6                      0.0           0.0   
2                        -17.7                      0.0           0.0   
3                        -17.6                      0.0           0.0   
4                        -18.6                      0.0           0.0   
...                        ...                      ...           ...   
8755                     -10.3                      0.0           0.0   
8756                      -9.9                      0.0           0.0   
8757                      -9.9                      0.0           0.0   
8758                      -9.8                      0.0           0.0   
8759                      -9.3                      0.0           0.0   

      Snowfall (cm) Seasons     Holiday Day of Week Weekend  
0               0.0  Winter  No Holiday      Friday      No  
1               0.0  Winter  No Holiday      Friday      No  
2               0.0  Winter  No Holiday      Friday      No  
3               0.0  Winter  No Holiday      Friday      No  
4               0.0  Winter  No Holiday      Friday      No  
...             ...     ...         ...         ...     ...  
8755            0.0  Autumn  No Holiday      Friday      No  
8756            0.0  Autumn  No Holiday      Friday      No  
8757            0.0  Autumn  No Holiday      Friday      No  
8758            0.0  Autumn  No Holiday      Friday      No  
8759            0.0  Autumn  No Holiday      Friday      No  

[8760 rows x 18 columns]

#### 3.2 합치기

In [54]:
df_fin = pd.concat([df_kaggle, df_new], axis=0)

df_fin

Date  Year Month Day  Rented Bike Count Hour  \
0               2017-12-01  2017    12   1              254.0    0   
1               2017-12-01  2017    12   1              204.0    1   
2               2017-12-01  2017    12   1              173.0    2   
3               2017-12-01  2017    12   1              107.0    3   
4               2017-12-01  2017    12   1               78.0    4   
...                    ...   ...   ...  ..                ...  ...   
44587  2023-12-31 20:00:00  2023    12  31                NaN   20   
44588  2023-12-31 21:00:00  2023    12  31                NaN   21   
44589  2023-12-31 22:00:00  2023    12  31                NaN   22   
44590  2023-12-31 23:00:00  2023    12  31                NaN   23   
44591  2024-01-01 00:00:00  2024    01  01                NaN   00   

       Temperature(℃)  Humidity(%)  Wind speed (m/s)  Visibility (10m)  \
0                -5.2         37.0               2.2            2000.0   
1                -5.5         38.0               0.8            2000.0   
2                -6.0         39.0               1.0            2000.0   
3                -6.2         40.0               0.9            2000.0   
4                -6.0         36.0               2.3            2000.0   
...               ...          ...               ...               ...   
44587             NaN          NaN               NaN               NaN   
44588             NaN          NaN               NaN               NaN   
44589             NaN          NaN               NaN               NaN   
44590             NaN          NaN               NaN               NaN   
44591             NaN          NaN               NaN               NaN   

       Dew point temperature(℃)  Solar Radiation (MJ/m2)  Rainfall(mm)  \
0                         -17.6                      0.0           0.0   
1                         -17.6                      0.0           0.0   
2                         -17.7                      0.0           0.0   
3                         -17.6                      0.0           0.0   
4                         -18.6                      0.0           0.0   
...                         ...                      ...           ...   
44587                       NaN                      NaN           NaN   
44588                       NaN                      NaN           NaN   
44589                       NaN                      NaN           NaN   
44590                       NaN                      NaN           NaN   
44591                       NaN                      NaN           NaN   

       Snowfall (cm) Seasons     Holiday Day of Week Weekend  
0                0.0  Winter  No Holiday      Friday      No  
1                0.0  Winter  No Holiday      Friday      No  
2                0.0  Winter  No Holiday      Friday      No  
3                0.0  Winter  No Holiday      Friday      No  
4                0.0  Winter  No Holiday      Friday      No  
...              ...     ...         ...         ...     ...  
44587            NaN  Winter  No Holiday      Sunday     Yes  
44588            NaN  Winter  No Holiday      Sunday     Yes  
44589            NaN  Winter  No Holiday      Sunday     Yes  
44590            NaN  Winter  No Holiday      Sunday     Yes  
44591            NaN  Winter     Holiday      Monday      No  

[53352 rows x 18 columns]